In [1]:
import sagemaker
from sagemaker.tensorflow.model import TensorFlowModel

model_dir = 's3://sagemaker-eu-west-1-291287855072/tf-sentiment-2021-10-26-19-32-40-757/output/model.tar.gz'
train_instance_type = 'ml.p3.8xlarge'
# train_instance_type = 'local'
# hyperparameters = {'epochs': 1, 'batch_size': 32, 'learning_rate': 0.01, 'training': 's3://sagemaker-eu-west-1-291287855072/Data/training/btc_train.csv', 'validation': 's3://sagemaker-eu-west-1-291287855072/Data/validation/btc_val.csv'}
hyperparameters = {'epochs': 1, 'batch_size': 32, 'learning_rate': 0.01}

transformer_model = TensorFlowModel(
                        model_data=model_dir,
                        role = sagemaker.get_execution_role(),
                        framework_version='2.1',
                        source_dir='./',
                        entry_point='model_deploy.py'
                      )

In [2]:
# a model deployed to a real-time endpoint via the deploy() command uses an estimator 
# a model deployed for serverless offline predictions with the transform() command uses transformer 
transformer = transformer_model.transformer(instance_count=1, instance_type='ml.c5.xlarge')

In [4]:
import numpy as np
import pandas as pd
import os

seq_len = 240
def get_test_data(test):
    test_data = pd.read_csv(test)
    test_data = test_data.head(480)
    test_data = test_data.values
    X_test, y_test = [], []
    for i in range(seq_len, len(test_data)):
        X_test.append(test_data[i-seq_len:i])
        y_test.append(test_data[:, 3][i])
    X_test, y_test = np.array(X_test), np.array(y_test)
    print('x test', X_test.shape,'y test', y_test.shape)
    return X_test, y_test

# Getting test npy files 
X_test, y_test = get_test_data('s3://cmajorsolo-transformerbucket/data/btc_test.csv')

# saving X_test, y_test as npy locally
import os
np.save(os.path.join('./Data', 'x_test_short.npy'), X_test)
np.save(os.path.join('./Data', 'y_test_short.npy'), y_test)

x test (240, 240, 6) y test (240,)


In [5]:
# Uploading testing npy data to S3
test_s3_prefix = 'Data/testing'
x_test_s3 = sagemaker.Session().upload_data(path='./Data/x_test_short.npy', key_prefix=test_s3_prefix)
print(x_test_s3)

y_test_s3 = sagemaker.Session().upload_data(path='./Data/y_test_short.npy', key_prefix=test_s3_prefix)
print(y_test_s3)

s3://sagemaker-eu-west-1-291287855072/Data/testing/x_test_short.npy
s3://sagemaker-eu-west-1-291287855072/Data/testing/y_test_short.npy


In [ ]:
transformer.transform('s3://sagemaker-eu-west-1-291287855072/Data/testing/x_test_short.npy', job_name='transformer-test-2')
transformer.wait()

.....................INFO:__main__:starting services
INFO:tfs_utils:using default model name: model
INFO:tfs_utils:tensorflow serving model config: 
model_config_list: {
  config: {
    name: "model",
    base_path: "/opt/ml/model",
    model_platform: "tensorflow"
  }
  config: {
    name: "model",
    base_path: "/opt/ml/model/code/model",
    model_platform: "tensorflow"
  }
}


INFO:__main__:using default model name: model
INFO:__main__:tensorflow serving model config: 
model_config_list: {
  config: {
    name: "model",
    base_path: "/opt/ml/model",
    model_platform: "tensorflow"
  }
  config: {
    name: "model",
    base_path: "/opt/ml/model/code/model",
    model_platform: "tensorflow"
  }
}


INFO:__main__:tensorflow version info:
TensorFlow ModelServer: 2.1.0-rc1+dev.sha.d80de10
TensorFlow Library: 2.1.1
INFO:__main__:tensorflow serving command: tensorflow_model_server --port=10000 --rest_api_port=10001 --model_config_file=/sagemaker/model-config.cfg --max_num_load_retrie

In [ ]:
import json

batch_output = transformer.output_path
!mkdir -p batch_data/output
!aws s3 cp --recursive $batch_output/ batch_data/output/

with open('batch_data/output/csv-test.csv.out', 'r') as f:
    jstr = json.load(f)
    results = [float('%.3f'%(item)) for sublist in jstr['predictions'] for item in sublist]
    print(results)

In [ ]:
# ToDo: get evaluation data 

In [55]:
inputs = {'training': 's3://sagemaker-eu-west-1-291287855072/Data/training/btc_train.csv', 'validation': 's3://sagemaker-eu-west-1-291287855072/Data/validation/btc_val.csv'}

In [3]:
# training_input_path = 's3://cmajorsolo-transformerbucket/data/btc_train.csv'
# test_data_uri = 's3://cmajorsolo-transformerbucket/data/btc_test.csv'
# validation_input_path = 's3://cmajorsolo-transformerbucket/data/btc_val.csv'
prefix = 'Data'

training_input_path   = sess.upload_data('Data/btc_train.csv', key_prefix=prefix+'/training')
validation_input_path = sess.upload_data('Data/btc_val.csv', key_prefix=prefix+'/validation')
inputs = {'training': training_input_path, 'validation': validation_input_path}
print(inputs)

{'training': 's3://sagemaker-eu-west-1-291287855072/Data/training/btc_train.csv', 'validation': 's3://sagemaker-eu-west-1-291287855072/Data/validation/btc_val.csv'}
